In [ ]:
# =============================================================================
# FORCE RELOAD MODULES (Run this cell if you made changes to imported modules)
# =============================================================================
import importlib
import sys

# Force reload of visualization modules
modules_to_reload = [
    'src.visualization.statistical_plots',
    'src.visualization.visualization_config', 
    'src.visualization.visualization_orchestrator',
    'src.visualization.intra_inter_distance_visualizations',
    'src.processing.branch_processing'
]

for module_name in modules_to_reload:
    if module_name in sys.modules:
        importlib.reload(sys.modules[module_name])
        print(f"Reloaded: {module_name}")
    else:
        print(f"Module not loaded: {module_name}")

print("Module reload complete!")


 Reloaded: src.visualization.statistical_plots
 Reloaded: src.visualization.visualization_config
 Reloaded: src.visualization.visualization_orchestrator
  Module not loaded: src.visualization.intra_inter_distance_visualizations
 Module reload complete!


# =============================================================================
# DENDRIC CLUSTERING ANALYSIS - MAIN NOTEBOOK
# =============================================================================
# This notebook performs comprehensive dendritic clustering analysis of neuronal
# synapse data, including excitatory/inhibitory synapse mapping, clustering,
# correlation analysis, and visualization.


In [10]:
# Find the project root (the folder that contains 'src' and 'config') and add it to sys.path
import sys
from pathlib import Path

def add_project_root(markers=("src", "config")):
    here = Path.cwd()
    for p in (here, *here.parents):
        if all((p / m).exists() for m in markers):
            sys.path.insert(0, str(p))
            print(" Project root added to sys.path:", p)
            return p
    raise RuntimeError("Could not locate project root with markers:", markers)

PROJECT_ROOT = add_project_root()


 Project root added to sys.path: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored


In [11]:
# =============================================================================
# 1. CONFIGURATION AND SETUP
# =============================================================================
# Load configuration from YAML file and set up project paths and parameters

from src.config import load_config
from src.utils import ensure_dir, set_seed
import importlib, src.config as cfgmod
importlib.reload(cfgmod)

from src.config import load_config, Paths
print("Paths dataclass fields:", Paths.__annotations__)  # should include 'interim_results_dir'
cfg = load_config("../config/default.yaml")
print(cfg.paths)


Paths dataclass fields: {'base_data': <class 'str'>, 'swc_dir': <class 'str'>, 'syn_dir': <class 'str'>, 'interim_results_dir': <class 'str'>}
Paths(base_data='data', swc_dir='data/microns/extracted_swc/SWC_Skel', syn_dir='data/microns/extracted_swc/syn', interim_results_dir='data/microns/intirim_results')


In [12]:
# =============================================================================
# 2. NEURON SKELETON LOADING
# =============================================================================
# Load and heal the SWC neuron skeleton file

from pathlib import Path
from src.io_swc import load_and_heal_swc

swc_dir_abs = (PROJECT_ROOT / cfg.paths.swc_dir).resolve()
swc_path = swc_dir_abs / f"{cfg.input.swc_prefix}{cfg.input.neuron_id}.swc"

print("SWC path:", swc_path, "exists:", swc_path.exists())

neuron = load_and_heal_swc(swc_path)
print("Neuron loaded:", neuron)

neuron.nodes


SWC path: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/data/microns/extracted_swc/SWC_Skel/microns_jan_n3.swc exists: True
Neuron loaded: type                                             navis.TreeNeuron
name                                               microns_jan_n3
id                           431c6796-76a6-46af-a686-6b24dc0c7b1c
n_nodes                                                     31521
n_connectors                                                 None
n_branches                                                    219
n_leafs                                                       230
cable_length                                          3213.320312
soma                                                         None
units                                                1 micrometer
created_at                             2025-09-17 11:57:42.198386
origin          /home/ge95zic/mnt/ge95zic/dendric_clustering/r...
file                                           microns_jan_

node_id label           x           y           z    radius  parent_id  \
0            1     0  651.012634  231.868530  906.797058  0.791176         -1   
1            2     0  662.086609  220.090561  895.135742  1.009817          4   
2            3     0  652.394836  226.683167  906.061157  1.217976      29273   
3            4     0  657.215271  213.973145  897.149963  3.298922        212   
4            5     0  563.103943  191.319458  847.732666  0.627453       1901   
...        ...   ...         ...         ...         ...       ...        ...   
31516    31517     0  703.483521  241.006805  859.725708  0.522779      31518   
31517    31518     0  703.466675  240.917740  859.672852  0.559932      31519   
31518    31519     0  703.449768  240.828690  859.619995  0.597086      31520   
31519    31520     0  703.432861  240.739624  859.567139  0.634239      31521   
31520    31521     0  703.415955  240.650558  859.514343  0.671392        367   

         type  
0        root  
1        slab  
2         end  
3      branch  
4        slab  
...       ...  
31516    slab  
31517    slab  
31518    slab  
31519    slab  
31520    slab  

[31521 rows x 8 columns]

In [13]:
# =============================================================================
# 4. SYNAPSE DATA LOADING AND PREPROCESSING
# =============================================================================
# Load synapse data, deduplicate, compute volumes, and split into E/I types

from pathlib import Path
from src.datasets.microns import build_syn_path, read_synapses_raw
from src.prep import (
    dedupe_raw_xyz,
    add_synapse_volume_nm3_to_um3,
    split_e_i_by_isOnSpine,
    normalized_from_raw,
    compute_volume_um3,
    drop_duplicate_positions,
)

# Build absolute path
syn_dir_abs = (PROJECT_ROOT / cfg.paths.syn_dir).resolve()
syn_path = build_syn_path(syn_dir_abs, cfg.input.syn_prefix, cfg.input.neuron_id)
print("Syn file:", syn_path)

# 1) Read raw synapse data
df_raw = read_synapses_raw(syn_path)

# 2) ORIGINAL PIPELINE (raw layer) - deduplicate and compute volumes
df_raw = dedupe_raw_xyz(df_raw, x="x", y="y", z="z")
df_raw = add_synapse_volume_nm3_to_um3(df_raw,
                                       syn_size_col="syn_size",
                                       out_col="SynapseVolume",
                                       dx_nm=cfg.voxel_nm.dx, dy_nm=cfg.voxel_nm.dy, dz_nm=cfg.voxel_nm.dz)
syn_exec_df, syn_inh_df = split_e_i_by_isOnSpine(df_raw)

# 3) NORMALIZED PIPELINE (for new functions) - standardize coordinate system
syn_df_norm = normalized_from_raw(df_raw, pos_unit="nm")
syn_df_norm = compute_volume_um3(syn_df_norm, dx_nm=cfg.voxel_nm.dx, dy_nm=cfg.voxel_nm.dy, dz_nm=cfg.voxel_nm.dz)
syn_df_norm = drop_duplicate_positions(syn_df_norm)

# Quick checks
print(f"All (raw, post-dedupe): {len(df_raw)} | E: {len(syn_exec_df)} | I: {len(syn_inh_df)}")
print("Normalized columns:", list(syn_df_norm.columns))
display(syn_exec_df.head())
display(syn_inh_df.head())


Syn file: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/data/microns/extracted_swc/syn/microns_jan_synn3.xlsx
All (raw, post-dedupe): 1423 | E: 959 | I: 464
Normalized columns: ['x_um', 'y_um', 'z_um', 'syn_size', 'is_on_spine', 'type', 'volume_um3']


Unnamed: 0     id     Epos3DX     Epos3DY  Epos3DZ  syn_size  \
1            1  30202  657.473904  178.620753   914.00     24780   
2            2  30501  700.190165  140.783739   915.72      8124   
7            7  19743  635.829279  185.255547   878.16     21756   
8            8  19350  664.358232  172.629965   890.64      6696   
12          12  24523  648.174247  161.826327   851.84      1132   

          pre_identity pre_type  isOnSpine  SynapseVolume  
1   864691135593788160  Unknown          0       0.099120  
2   864691135994517376  Unknown          0       0.032496  
7   864691135048467328  Unknown          0       0.087024  
8   864691136585704960  Unknown          0       0.026784  
12  864691135469724288      DTC          0       0.004528

Unnamed: 0     id     Ipos3DX     Ipos3DY  Ipos3DZ  syn_size  \
0           0   6402  709.784696  228.465614   882.92     15004   
3           3  11853  621.166912  257.018718   897.28      4112   
4           4  23503  643.704676  157.564561   890.00       392   
5           5  19873  638.696607  157.254900   834.36      8300   
6           6  17974  640.330171   33.759337   832.32       160   

         pre_identity pre_type  isOnSpine  SynapseVolume  
0  864691135403564800  Unknown          1       0.060016  
3  864691136585348608  Unknown          1       0.016448  
4  864691135437611008  Unknown          1       0.001568  
5  864691135469724288      DTC          1       0.033200  
6  864691135453276288  Unknown          1       0.000640

In [14]:
# =============================================================================
# 5. SYNAPSE-TO-NODE MAPPING
# =============================================================================
# Map excitatory synapses to their closest skeleton nodes and compute statistics

import numpy as np
from src.processing.synapse_mapping import (
    map_synapses_to_nodes,
    compute_synapse_node_statistics,
    create_node_counts_series
)

# Map excitatory synapses to nodes
syn_exec_df = map_synapses_to_nodes(
    neuron, syn_exec_df, 
    coord_cols=("Epos3DX", "Epos3DY", "Epos3DZ"),
    method="brute_force"
)

# Compute mapping statistics
mapping_stats = compute_synapse_node_statistics(syn_exec_df)
print("Excitatory synapse mapping statistics:")
for key, value in mapping_stats.items():
    print(f"  {key}: {value}")

# Create node counts series aligned with neuron skeleton
node_counts = create_node_counts_series(syn_exec_df, neuron)

# Map inhibitory synapses to nodes (for later analysis)
syn_inh_df = map_synapses_to_nodes(
    neuron, syn_inh_df,
    coord_cols=("Ipos3DX", "Ipos3DY", "Ipos3DZ"),
    method="brute_force"
)

print(f"\nInhibitory synapses mapped to {len(syn_inh_df['closest_node_id'].unique())} unique nodes")

# =============================================================================
# ADD DISTANCE TO SOMA PROPERTY
# =============================================================================
# Add distance_to_soma property to both excitatory and inhibitory synapse dataframes




Excitatory synapse mapping statistics:
  n_unique_nodes_with_synapses: 907
  max_synapses_per_node: 4
  max_synapses_node_id: 1
  avg_synapses_per_node: 1.0573318632855568
  median_synapses_per_node: 1.0
  total_synapses: 959

Inhibitory synapses mapped to 452 unique nodes


In [15]:
# =============================================================================
# 6. GEODESIC DISTANCE MATRIX COMPUTATION
# =============================================================================
# Compute or load cached geodesic distance matrix between all skeleton nodes

import navis
import os, pickle
from src.geo import compute_or_load_geodesic

# Build cache directory
interim_dir = (PROJECT_ROOT / cfg.paths.interim_results_dir).resolve()
interim_dir.mkdir(parents=True, exist_ok=True)

# Compute or load geodesic matrix
geodesic_mat_full = compute_or_load_geodesic(
    neuron, interim_dir, cfg.input.neuron_id, force_recompute=False
)

print(f"Geodesic matrix shape: {geodesic_mat_full.shape}")
print(f"Matrix type: {type(geodesic_mat_full)}")

# Check for infinite values
arr = geodesic_mat_full.values if hasattr(geodesic_mat_full, "values") else geodesic_mat_full
if np.isinf(arr).any():
    print(" The geodesic matrix contains infinite values.")
else:
    print(" Geodesic matrix is valid (no infinite values)")

geodesic_mat_full


Found geodesic cache: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/data/microns/intirim_results/geodesic_mat_n3.pkl → loading
 Geodesic matrix contains ∞ values.
Geodesic matrix shape: (31521, 31521)
Matrix type: <class 'pandas.core.frame.DataFrame'>
 The geodesic matrix contains infinite values.


1          2      3           4           5           6      \
1        0.0        inf    inf         inf         inf         inf   
2        inf   0.000000    inf         inf         inf         inf   
3        inf        inf    0.0         inf         inf         inf   
4        inf        inf    inf    0.000000  148.487333  148.488960   
5        inf        inf    inf  148.487333    0.000000    0.204895   
...      ...        ...    ...         ...         ...         ...   
31517    inf  68.067249    inf         inf         inf         inf   
31518    inf  67.962319    inf         inf         inf         inf   
31519    inf  67.857393    inf         inf         inf         inf   
31520    inf  67.752453    inf         inf         inf         inf   
31521    inf  67.647544    inf         inf         inf         inf   

            7           8           9           10     ...      31512  \
1             inf         inf         inf         inf  ...        inf   
2             inf         inf         inf         inf  ...  68.591893   
3             inf         inf         inf         inf  ...        inf   
4      129.505555  129.507832  129.506371  136.053309  ...        inf   
5      277.992889  277.995165  277.993704   12.639064  ...        inf   
...           ...         ...         ...         ...  ...        ...   
31517         inf         inf         inf         inf  ...   0.524644   
31518         inf         inf         inf         inf  ...   0.629574   
31519         inf         inf         inf         inf  ...   0.734501   
31520         inf         inf         inf         inf  ...   0.839440   
31521         inf         inf         inf         inf  ...   0.944349   

           31513      31514      31515      31516      31517      31518  \
1            inf        inf        inf        inf        inf        inf   
2      68.486954  68.382024  68.277097  68.172189  68.067249  67.962319   
3            inf        inf        inf        inf        inf        inf   
4            inf        inf        inf        inf        inf        inf   
5            inf        inf        inf        inf        inf        inf   
...          ...        ...        ...        ...        ...        ...   
31517   0.419705   0.314775   0.209848   0.104940   0.000000   0.104930   
31518   0.524635   0.419705   0.314778   0.209869   0.104930   0.000000   
31519   0.629561   0.524631   0.419705   0.314796   0.209856   0.104927   
31520   0.734501   0.629571   0.524644   0.419736   0.314796   0.209866   
31521   0.839410   0.734480   0.629553   0.524644   0.419705   0.314775   

           31519      31520      31521  
1            inf        inf        inf  
2      67.857393  67.752453  67.647544  
3            inf        inf        inf  
4            inf        inf        inf  
5            inf        inf        inf  
...          ...        ...        ...  
31517   0.209856   0.314796   0.419705  
31518   0.104927   0.209866   0.314775  
31519   0.000000   0.104940   0.209848  
31520   0.104940   0.000000   0.104909  
31521   0.209848   0.104909   0.000000  

[31521 rows x 31521 columns]

In [16]:
# =============================================================================
# 7. GAUSSIAN KERNEL WEIGHT MATRIX COMPUTATION
# =============================================================================
# Compute Gaussian kernel weight matrix for synapse density smoothing

import pickle
import os
from src.geo import compute_or_load_node_kernel

# Compute or load node kernel weight matrix
W_nodes, W_nodes_normalized = compute_or_load_node_kernel(
    geodesic_mat_full, interim_dir, cfg.input.neuron_id, 
    cfg.analysis.sigma_um, force_recompute=False
)

print(f"Weight matrix shape: {W_nodes.shape}")
print(f"Weight matrix type: {type(W_nodes)}")
print(f"Sigma parameter: {cfg.analysis.sigma_um} μm")

# Check matrix properties
if hasattr(W_nodes, 'values'):
    # If it's a pandas DataFrame, get the underlying numpy array
    W_values = W_nodes.values
else:
    # If it's already a numpy array
    W_values = W_nodes

print(f"Min weight: {W_values.min():.6f}")
print(f"Max weight: {W_values.max():.6f}")
print(f"Mean weight: {W_values.mean():.6f}")

print(" Gaussian kernel weight matrix computed successfully")


Found file: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/data/microns/intirim_results/node_weight_mat_n3_sigma:1.0.pkl. Loading node weight matrix...
Weight matrix shape: (31521, 31521)
Weight matrix type: <class 'pandas.core.frame.DataFrame'>
Sigma parameter: 1.0 μm
Min weight: 0.000000
Max weight: 1.000000
Mean weight: 0.000825
 Gaussian kernel weight matrix computed successfully


In [17]:
# =============================================================================
# 8. SYNAPSE DENSITY COMPUTATION AND GRADIENT-ASCENT CLUSTERING
# =============================================================================
# Compute synapse densities and perform gradient-ascent clustering

from src.density import node_density_from_counts, attach_density_to_nodes
from src.clustering import (
    add_synapse_counts,
    get_local_maximum,
    group_by_peak,
    summarize_clusters,
    add_peak_node_to_calculation_nodes,
)

# 1) Compute synapse density for each node
# This calculates the density per node using the Gaussian kernel weight matrix
# W_nodes_normalized.dot(node_counts) gives the smoothed synapse density
node_density = node_density_from_counts(W_nodes_normalized, node_counts)

# Print density statistics matching the original dc_initial_algo.py format
print(f"Maximum density: {node_density.max():.3f}")
print(f"Average density: {node_density.mean():.3f}") 
print(f"Minimum density: {node_density.min():.3f}")
print(f"Computed synapse density for {len(node_density)} nodes")

# 2) Attach density to neuron nodes
# This creates calculation_nodes with synapse_density column, matching original code
calculation_nodes = attach_density_to_nodes(neuron, node_density)
print(f"Attached density to {len(calculation_nodes)} nodes")

# 3) Add synapse counts to calculation nodes
calculation_nodes = add_synapse_counts(calculation_nodes, node_counts)

# 4) Use only nodes with synapses (>0) for clustering
synapse_node_list = calculation_nodes.loc[calculation_nodes["synapse_count"] > 0, "node_id"].tolist()
print(f"Nodes with synapses: {len(synapse_node_list)}")

# 5) Perform gradient-ascent clustering to find local density maxima
peaks = get_local_maximum(neuron, calculation_nodes, synapse_node_list)
peaks = {int(k): int(v) for k, v in peaks.items()}

# 6) Group nodes by their peak
clusters_dict = group_by_peak(peaks)

# 6.5) Add peak_node column to calculation_nodes
calculation_nodes = add_peak_node_to_calculation_nodes(calculation_nodes, clusters_dict)
print(f"Added peak_node column to calculation_nodes. Columns: {list(calculation_nodes.columns)}")

# 7) Summarize clustering results
summary = summarize_clusters(clusters_dict)
print("\nClustering Results:")
print(f"  Number of clusters: {summary['n_clusters']}")
print(f"  Largest cluster peak: {summary['largest_peak']}")
print(f"  Largest cluster size: {summary['largest_count']} nodes")
print(f"  Total assigned nodes: {summary['total_assigned_nodes']}")

# 8) Sanity check
total_nodes = sum(len(nodes) for nodes in clusters_dict.values())
print(f"  Sanity check - total nodes: {total_nodes}")

print(" Gradient-ascent clustering completed successfully")


Maximum density: 2.560
Average density: 0.285
Minimum density: 0.000
Computed synapse density for 31521 nodes
Attached density to 31521 nodes
Nodes with synapses: 907


Nodes processed:   0%|          | 0/907 [00:00<?, ?it/s]

Added peak_node column to calculation_nodes. Columns: ['node_id', 'label', 'x', 'y', 'z', 'radius', 'parent_id', 'type', 'synapse_density', 'synapse_count', 'peak_node']

Clustering Results:
  Number of clusters: 586
  Largest cluster peak: 13795
  Largest cluster size: 7 nodes
  Total assigned nodes: 907
  Sanity check - total nodes: 907
 Gradient-ascent clustering completed successfully


In [141]:
# =============================================================================
# 9. CLUSTER PROCESSING AND METRICS COMPUTATION
# =============================================================================
# Build cluster DataFrame and compute cluster metrics

# Force reload of the module to get updated code
import importlib
import src.processing.cluster_processing as cluster_processing
importlib.reload(cluster_processing)

from src.processing.cluster_processing import (
    build_cluster_dataframe,
    compute_cluster_metrics,
    filter_clusters_by_density,
    print_cluster_statistics
)

# 1) Create cluster ID mappings
unique_peaks = sorted(clusters_dict.keys())
peak_to_cluster_id = {peak: idx for idx, peak in enumerate(unique_peaks, start=0)}
new_cluster_id_to_peak = {new_id: peak for peak, new_id in peak_to_cluster_id.items()}

# 2) Assign cluster IDs to synapses and nodes
syn_exec_df["cluster_id"] = syn_exec_df["closest_node_id"].map(peaks).map(peak_to_cluster_id)
calculation_nodes["cluster_id"] = calculation_nodes["node_id"].map(peaks).map(peak_to_cluster_id)

# 3) Build cluster DataFrame
cluster_df = build_cluster_dataframe(
    syn_exec_df, clusters_dict, peak_to_cluster_id, new_cluster_id_to_peak, syn_id_col="id"
)

# 4) Compute cluster metrics (cable length, density)
cluster_df = compute_cluster_metrics(
    cluster_df, syn_exec_df, geodesic_mat_full, neuron
)

# 5) Filter clusters by density threshold
overall_density = len(syn_exec_df) / neuron.cable_length
cluster_df = filter_clusters_by_density(cluster_df, overall_density, min_density_factor=1.0)

print(f"\nCluster Processing Results:")
print(f"  Total clusters found: {len(unique_peaks)}")
print(f"  Clusters after density filtering: {len(cluster_df)}")
print(f"  Overall synapse density: {overall_density:.5f} synapses/μm")

# Print comprehensive cluster statistics
print_cluster_statistics(cluster_df)

print(" Cluster processing completed successfully")


Filtered clusters: 586 -> 206
Density threshold: 0.29845

Cluster Processing Results:
  Total clusters found: 586
  Clusters after density filtering: 206
  Overall synapse density: 0.29845 synapses/μm

CLUSTER STATISTICS

 SYNAPSE COUNT:
  Max  # syn:   8
  Mean # syn:   2.70
  Median # syn: 2.0
  Min  # syn:   2
  Std  # syn:   1.04

 CLUSTER DENSITY (synapses/μm):
  Max  density:   26.534
  Mean density:   3.110
  Median density: 1.751
  Min  density:   0.687
  Std  density:   4.184

 MINIMAL CABLE LENGTH (μm):
  Max  length:   7.610
  Mean length:   1.672
  Median length: 1.424
  Min  length:   0.079
  Std  length:   1.279

 SUMMARY:
  Total clusters: 206
  Total synapses: 557
  Total cable length: 344.45 μm
  Overall density: 1.617 synapses/μm
 Cluster processing completed successfully


In [142]:
# =============================================================================
# 10. INHIBITORY SYNAPSE ANALYSIS
# =============================================================================
# Analyze inhibitory synapses and their relationship to excitatory clusters

# 1) Compute inhibitory synapse density and clustering
node_counts_inh = create_node_counts_series(syn_inh_df, neuron, 'closest_node_id')
node_density_inh = node_density_from_counts(W_nodes_normalized, node_counts_inh)
calculation_nodes_inh = attach_density_to_nodes(neuron, node_density_inh)
calculation_nodes_inh = add_synapse_counts(calculation_nodes_inh, node_counts_inh)

# 2) Perform gradient-ascent clustering for inhibitory synapses
synapse_node_list_inh = calculation_nodes_inh.loc[calculation_nodes_inh["synapse_count"] > 0, "node_id"].tolist()
peaks_inh = get_local_maximum(neuron, calculation_nodes_inh, synapse_node_list_inh)
peaks_inh = {int(k): int(v) for k, v in peaks_inh.items()}
clusters_dict_inh = group_by_peak(peaks_inh)

# 2.5) Add peak_node column to calculation_nodes_inh
calculation_nodes_inh = add_peak_node_to_calculation_nodes(calculation_nodes_inh, clusters_dict_inh)
print(f"Added peak_node column to calculation_nodes_inh. Columns: {list(calculation_nodes_inh.columns)}")

# 3) Create inhibitory cluster ID mappings (similar to excitatory)
unique_peaks_inh = sorted(clusters_dict_inh.keys())
peak_to_cluster_id_inh = {peak: idx for idx, peak in enumerate(unique_peaks_inh, start=0)}
new_cluster_id_to_peak_inh = {new_id: peak for peak, new_id in peak_to_cluster_id_inh.items()}

# 4) Assign inhibitory cluster IDs to synapses and nodes
syn_inh_df["cluster_id"] = syn_inh_df["closest_node_id"].map(peaks_inh).map(peak_to_cluster_id_inh)
calculation_nodes_inh["cluster_id"] = calculation_nodes_inh["node_id"].map(peaks_inh).map(peak_to_cluster_id_inh)

# 5) Build inhibitory cluster DataFrame
syn_inh_cluster_df = build_cluster_dataframe(
    syn_inh_df, clusters_dict_inh, peak_to_cluster_id_inh, new_cluster_id_to_peak_inh, syn_id_col="id"
)

# 6) Compute inhibitory cluster metrics (cable length, density)
syn_inh_cluster_df = compute_cluster_metrics(
    syn_inh_cluster_df, syn_inh_df, geodesic_mat_full, neuron
)

print(f"\nInhibitory Analysis Results:")
print(f"  Inhibitory clusters found: {len(clusters_dict_inh)}")
print(f"  Inhibitory synapses: {len(syn_inh_df)}")

# Add distance_to_soma property to inhibitory cluster dataframe

print(" Inhibitory synapse analysis completed successfully")


Nodes processed:   0%|          | 0/452 [00:00<?, ?it/s]

Added peak_node column to calculation_nodes_inh. Columns: ['node_id', 'label', 'x', 'y', 'z', 'radius', 'parent_id', 'type', 'synapse_density', 'synapse_count', 'peak_node']

Inhibitory Analysis Results:
  Inhibitory clusters found: 328
  Inhibitory synapses: 464
 Inhibitory synapse analysis completed successfully


cluster_id  Cluster_Peak  e_synapse_count               Synapses  \
0             0             4                2         [17252, 17252]   
1             1            54                1                 [8412]   
2             2           178                1                [26437]   
3             3           218                1                [21667]   
4             4           250                2           [9153, 9151]   
..          ...           ...              ...                    ...   
323         323         31272                1                [31261]   
324         324         31294                2         [31283, 31295]   
325         325         31387                3  [31381, 31391, 31372]   
326         326         31427                1                [31412]   
327         327         31491                1                [31487]   

          Associated_Nodes  minimal_cable_length  cluster_density  
0                      [2]              0.000000         0.000000  
1                     [54]              0.000000         0.000000  
2                    [178]              0.000000         0.000000  
3                  [21818]              0.000000         0.000000  
4             [9469, 9471]              0.200680         9.966110  
..                     ...                   ...              ...  
323                [31266]              0.000000         0.000000  
324         [31288, 31300]              1.201796         1.664176  
325  [31377, 31386, 31396]              1.900498         1.578534  
326                [31417]              0.000000         0.000000  
327                [31490]              0.000000         0.000000  

[328 rows x 7 columns]

In [ ]:
# =============================================================================
# 11. E/I DISTANCE-BASED MAPPING
# =============================================================================
# Map inhibitory synapses to excitatory clusters based on distance analysis
import importlib
import src.processing.distance_analysis as distance_analysis
importlib.reload(distance_analysis)
from src.processing.distance_analysis import (
    find_closest_excitatory_synapses,
    map_inhibitory_to_excitatory_clusters_by_distance,
    split_mixed_inhibitory_clusters_by_distance,
    compute_distances_within_clusters,
    analyze_e_i_relationships,
    compute_distance_statistics,
    define_cutoff_strategies,
    apply_distance_cutoff,
    print_distance_analysis_summary
)

# 1) Find closest excitatory synapses for each inhibitory synapse
print("Finding closest excitatory synapses for inhibitory synapses...")
syn_inh_df = find_closest_excitatory_synapses(syn_inh_df, syn_exec_df, geodesic_mat_full)

# 2) Map inhibitory synapses to excitatory clusters by distance
print("Mapping inhibitory synapses to excitatory clusters...")
valid_exec_ids = set(cluster_df["cluster_id"])
syn_inh_df = map_inhibitory_to_excitatory_clusters_by_distance(
    syn_inh_df, syn_exec_df, cluster_df
)

# 3) Split mixed inhibitory clusters
print("Splitting mixed inhibitory clusters...")
syn_inh_df = split_mixed_inhibitory_clusters_by_distance(syn_inh_df, valid_exec_ids)

# 4) Compute distances within clusters
print("Computing distances within clusters...")
syn_inh_df = compute_distances_within_clusters(syn_inh_df, syn_exec_df, geodesic_mat_full)



# 6) Compute distance statistics
print("Computing distance statistics...")
distance_stats = compute_distance_statistics(syn_inh_df)

# 7) Define cutoff strategies
cutoff_strategies = define_cutoff_strategies(distance_stats)

# 8) Apply distance cutoff (using dynamic cutoff based on overall density as in dc_initial_algo.py)
# Calculate dynamic cutoff: 1.00 / overall_density (following dc_initial_algo.py)
dynamical_cutoff = 1.00 / overall_density
print(f"Dynamic cutoff (1.00/overall_density): {dynamical_cutoff:.3f} μm")
print(f"Median cutoff: {cutoff_strategies['median']:.3f} μm")

# Use dynamic cutoff instead of median
cutoff_threshold = dynamical_cutoff
syn_inh_df_filtered = apply_distance_cutoff(syn_inh_df, cutoff_threshold)

# 9) Print comprehensive summary (without E/I relationship analysis)
print("=" * 80)
print("DISTANCE ANALYSIS SUMMARY")
print("=" * 80)

print(f"\n DISTANCE STATISTICS:")
print(f"   Total inhibitory synapses with valid distances: {distance_stats['total_synapses']}")
print(f"   Mean distance to closest E-synapse: {distance_stats['mean_distance']:.3f} μm")
print(f"   Median distance to closest E-synapse: {distance_stats['median_distance']:.3f} μm")
print(f"   Max distance to closest E-synapse: {distance_stats['max_distance']:.3f} μm")
print(f"   Min distance to closest E-synapse: {distance_stats['min_distance']:.3f} μm")
print(f"   Std distance to closest E-synapse: {distance_stats['std_distance']:.3f} μm")

print(f"\n FILTERING RESULTS:")
print(f"   Original inhibitory synapses: {len(syn_inh_df)}")
print(f"   Synapses with valid E-mapping: {len(syn_inh_df)}")
print(f"   Synapses after distance cutoff: {len(syn_inh_df_filtered)}")
print(f"   Filtering efficiency: {len(syn_inh_df_filtered)/len(syn_inh_df)*100:.1f}%")

print(f"\n CUTOFF STRATEGY:")
print(f"   Strategy: dynamic")
print(f"   Threshold: {cutoff_threshold:.3f} μm")
print("=" * 80)

print(" E/I distance-based mapping completed successfully")


Finding closest excitatory synapses for inhibitory synapses...


In [145]:
# =============================================================================
# 12. UPDATE SYNAPSE DATAFRAMES AFTER FILTERING
# =============================================================================
# Update syn_exec_df and syn_inh_df to reflect which clusters got filtered out

print("Updating synapse dataframes after cluster filtering...")

# 1) Update syn_exec_df to only include synapses in valid clusters
valid_cluster_ids = set(cluster_df['cluster_id'])
syn_exec_df_filtered = syn_exec_df[syn_exec_df['cluster_id'].isin(valid_cluster_ids)].copy()
print(f"E synapses: {len(syn_exec_df)} -> {len(syn_exec_df_filtered)} (filtered)")

# 2) syn_inh_df_filtered is already created in cell 11 (E/I distance-based mapping)
# No need to recreate it or merge with itself - it already contains all the necessary columns
print(f"I synapses: {len(syn_inh_df)} -> {len(syn_inh_df_filtered)} (filtered)")

# 3) Add I synapse cluster information to syn_exec_df_filtered
# This adds information about which I cluster each E synapse is closest to
print("Adding I synapse cluster information to E synapse dataframe...")

# Get the I synapse cluster information for each E cluster
e_cluster_i_cluster_info = syn_inh_df_filtered.groupby('cluster_id_exec').agg({
    'cluster_id_inh': 'first',  # Get the I cluster ID
    'min_dist_e_syn_in_clu': 'min'  # Get the minimum distance
}).reset_index()
e_cluster_i_cluster_info.columns = ['cluster_id', 'closest_i_cluster_id', 'min_dist_to_i_synapse']

# Merge this information with syn_exec_df_filtered
syn_exec_df_filtered = syn_exec_df_filtered.merge(
    e_cluster_i_cluster_info, 
    on='cluster_id', 
    how='left'
)

print(" Synapse dataframes updated after filtering")

Updating synapse dataframes after cluster filtering...
E synapses: 959 -> 557 (filtered)
I synapses: 464 -> 146 (filtered)
Adding I synapse cluster information to E synapse dataframe...
 Synapse dataframes updated after filtering


Updating synapse dataframes after cluster filtering...
E synapses: 959 -> 557 (filtered)
I synapses: 464 -> 146 (filtered)
Adding I synapse cluster information to E synapse dataframe...
 Synapse dataframes updated after filtering


In [ ]:
# =============================================================================
# 13. ENHANCED CLUSTER DATAFRAMES
# =============================================================================
# Create enhanced cluster dataframes with I synapse counts and additional properties

print("Creating enhanced cluster dataframes...")

# 1) Add I synapse counts to excitatory cluster_df
print("Adding I synapse counts to excitatory cluster dataframe...")

# Rename cluster_id to e_cluster_id for clarity
cluster_df = cluster_df.rename(columns={'cluster_id': 'e_cluster_id'})


# Count I synapses mapped to each E cluster
i_synapse_counts = syn_inh_df_filtered.groupby('cluster_id_exec').size().to_dict()
cluster_df['i_synapse_count'] = cluster_df['e_cluster_id'].map(i_synapse_counts).fillna(0).astype(int)

cluster_df["has_I_associated"] = cluster_df["i_synapse_count"] > 0
# Count I clusters mapped to each E cluster
i_cluster_counts = syn_inh_df_filtered.groupby('cluster_id_exec')['cluster_id_inh'].nunique().to_dict()
cluster_df['i_cluster_count'] = cluster_df['e_cluster_id'].map(i_cluster_counts).fillna(0).astype(int)

# 2) Create filtered inhibitory cluster dataframe
print("Creating filtered inhibitory cluster dataframe...")
syn_inh_cluster_df_filtered = syn_inh_df_filtered.groupby('cluster_id_inh').agg(
    i_synapse_count=('cluster_id_inh', 'size'),
    i_synapses=('id', lambda x: list(x)),
    mapped_e_cluster=('cluster_id_exec', 'first'),
    min_distance_to_e=('min_dist_e_syn_in_clu', 'min'),
    mean_distance_to_e=('min_dist_e_syn_in_clu', 'mean'),
    max_distance_to_e=('min_dist_e_syn_in_clu', 'max')
).reset_index()

# Rename cluster_id_inh to i_cluster_id for clarity
syn_inh_cluster_df_filtered = syn_inh_cluster_df_filtered.rename(columns={'cluster_id_inh': 'i_cluster_id'})

# 3) Create final I cluster assessment dataframe
print("Creating final I cluster assessment dataframe...")
final_i_cluster_df = syn_inh_cluster_df_filtered.copy()
final_i_cluster_df['e_cluster_id'] = final_i_cluster_df['mapped_e_cluster']
final_i_cluster_df = final_i_cluster_df.merge(
    cluster_df[['e_cluster_id', 'e_synapse_count', 'cluster_density', 'minimal_cable_length']], 
    left_on='e_cluster_id', 
    right_on='e_cluster_id', 
    how='left',
    suffixes=('', '_e')
)

# Add E/I ratio
final_i_cluster_df['e_i_ratio'] = final_i_cluster_df['e_synapse_count'] / final_i_cluster_df['i_synapse_count']
final_i_cluster_df['e_i_ratio'] = final_i_cluster_df['e_i_ratio'].replace([np.inf, -np.inf], np.nan)

# Remove redundant columns to avoid duplication
# Remove the old 'mapped_e_cluster' column since we now have 'e_cluster_id'
final_i_cluster_df = final_i_cluster_df.drop(columns=['mapped_e_cluster'])

print(" Enhanced cluster dataframes created successfully")

# Print summary statistics
print(f"\nEnhanced Cluster DataFrames Created:")
print(f"  Enhanced cluster_df shape: {cluster_df.shape}")
print(f"  syn_inh_cluster_df_filtered shape: {syn_inh_cluster_df_filtered.shape}")
print(f"  final_i_cluster_df shape: {final_i_cluster_df.shape}")

print(f"\nE Cluster Statistics:")
print(f"  E clusters with I synapses: {len(cluster_df[cluster_df['i_synapse_count'] > 0])}")
print(f"  Total I synapses mapped: {cluster_df['i_synapse_count'].sum()}")
print(f"  Total I clusters mapped: {cluster_df['i_cluster_count'].sum()}")

print(f"\nI Cluster Statistics:")
print(f"  I clusters after filtering: {len(syn_inh_cluster_df_filtered)}")
print(f"  I clusters with valid E mapping: {len(final_i_cluster_df[final_i_cluster_df['e_cluster_id'].notna()])}")
print(f"  Mean I cluster size: {syn_inh_cluster_df_filtered['i_synapse_count'].mean():.2f}")
print(f"  Mean distance to E synapses: {syn_inh_cluster_df_filtered['mean_distance_to_e'].mean():.2f} μm")

# Add distance_to_soma property to filtered inhibitory cluster dataframe
print("\nAdding distance_to_soma property to filtered inhibitory cluster dataframe...")

# Get geodesic distances to soma (node 1)
geodesic_to_soma = geodesic_mat_full[1]

# Add distance_to_soma to excitatory synapses
syn_exec_df["distance_to_soma"] = (
    syn_exec_df["distance_to_node"] 
    + syn_exec_df["closest_node_id"].map(geodesic_to_soma)
)

# Add distance_to_soma to inhibitory synapses
syn_inh_df["distance_to_soma"] = (
    syn_inh_df["distance_to_node"] 
    + syn_inh_df["closest_node_id"].map(geodesic_to_soma)
)



syn_inh_df_filtered["distance_to_soma"] = (
    syn_inh_df_filtered["distance_to_node"] 
    + syn_inh_df_filtered["closest_node_id"].map(geodesic_to_soma)
)

syn_exec_df.rename(columns={"Unnamed: 0": "Exec_syn_id"}, inplace=True)
syn_inh_df.rename(columns={"Unnamed: 0": "Inh_syn_id"}, inplace=True)


print(f"Distance to soma property added to:")
print(f"  - Excitatory synapses: {len(syn_exec_df)} synapses")
print(f"  - Inhibitory synapses: {len(syn_inh_df)} synapses")

Creating enhanced cluster dataframes...
Adding I synapse counts to excitatory cluster dataframe...
Creating filtered inhibitory cluster dataframe...
Creating final I cluster assessment dataframe...
 Enhanced cluster dataframes created successfully

Enhanced Cluster DataFrames Created:
  Enhanced cluster_df shape: (206, 10)
  syn_inh_cluster_df_filtered shape: (121, 7)
  final_i_cluster_df shape: (121, 11)

E Cluster Statistics:
  E clusters with I synapses: 101
  Total I synapses mapped: 146
  Total I clusters mapped: 121

I Cluster Statistics:
  I clusters after filtering: 121
  I clusters with valid E mapping: 121
  Mean I cluster size: 1.21
  Mean distance to E synapses: 1.12 μm

Adding distance_to_soma property to filtered inhibitory cluster dataframe...
Distance to soma property added to:
  - Excitatory synapses: 959 synapses
  - Inhibitory synapses: 464 synapses


In [ ]:
# =============================================================================
# 14. DATAFRAME DESCRIPTIONS AND COMPACT SUMMARY
# =============================================================================
# Explain what each dataframe represents and provide compact summary statistics
import importlib
import src.processing.cluster_processing as cluster_processing
importlib.reload(cluster_processing)
from src.processing.cluster_processing import (
    compute_separated_cluster_statistics,
    print_separated_cluster_summary
)

print("=" * 80)
print("DATAFRAME DESCRIPTIONS")
print("=" * 80)

print(f"\n cluster_df:")
print(f"  Description: Excitatory clusters with their properties and I synapse counts")
print(f"  Shape: {cluster_df.shape}")
print(f"  Key columns: e_cluster_id, e_synapse_count, cluster_density, minimal_cable_length, i_synapse_count, i_cluster_count")

print(f"\n syn_inh_cluster_df_filtered:")
print(f"  Description: Inhibitory clusters after distance filtering with E cluster mapping")
print(f"  Shape: {syn_inh_cluster_df_filtered.shape}")
print(f"  Key columns: i_cluster_id, i_synapse_count, mapped_e_cluster, min/mean/max_distance_to_e")

print(f"\n final_i_cluster_df:")
print(f"  Description: Complete I cluster assessment with E cluster properties and E/I ratios")
print(f"  Shape: {final_i_cluster_df.shape}")
print(f"  Key columns: i_cluster_id, i_synapse_count, e_cluster_id, e_synapse_count, e_i_ratio, distance metrics")

print(f"\n syn_inh_df_filtered:")
print(f"  Description: Individual inhibitory synapses after distance filtering")
print(f"  Shape: {syn_inh_df_filtered.shape}")
print(f"  Key columns: id, cluster_id_inh, cluster_id_exec, min_dist_e_syn_in_clu")

# Compute separated cluster statistics
separated_stats = compute_separated_cluster_statistics(cluster_df)

# Print separated cluster summary
print_separated_cluster_summary(separated_stats)

# Overall E/I association summary
print(f"\n OVERALL E/I ASSOCIATION:")
print(f"  E clusters with I synapses: {len(cluster_df[cluster_df['i_synapse_count'] > 0])}")
print(f"  E clusters without I synapses: {len(cluster_df[cluster_df['i_synapse_count'] == 0])}")
print(f"  Total I synapses mapped: {cluster_df['i_synapse_count'].sum()}")
print(f"  Mean E/I ratio: {final_i_cluster_df['e_i_ratio'].mean():.2f}")

print("\n" + "=" * 80)
print(" SUMMARY COMPLETED")
print("=" * 80)


DATAFRAME DESCRIPTIONS

 cluster_df:
  Description: Excitatory clusters with their properties and I synapse counts
  Shape: (206, 10)
  Key columns: e_cluster_id, e_synapse_count, cluster_density, minimal_cable_length, i_synapse_count, i_cluster_count

 syn_inh_cluster_df_filtered:
  Description: Inhibitory clusters after distance filtering with E cluster mapping
  Shape: (121, 7)
  Key columns: i_cluster_id, i_synapse_count, mapped_e_cluster, min/mean/max_distance_to_e

 final_i_cluster_df:
  Description: Complete I cluster assessment with E cluster properties and E/I ratios
  Shape: (121, 11)
  Key columns: i_cluster_id, i_synapse_count, e_cluster_id, e_synapse_count, e_i_ratio, distance metrics

 syn_inh_df_filtered:
  Description: Individual inhibitory synapses after distance filtering
  Shape: (146, 20)
  Key columns: id, cluster_id_inh, cluster_id_exec, min_dist_e_syn_in_clu
COMPACT CLUSTER SUMMARY (SEPARATED BY I SYNAPSE ASSOCIATION)

 E CLUSTERS WITH I SYNAPSES (n=101):
   CLUS

In [ ]:
# =============================================================================
# 15. COMPREHENSIVE FILTERING SUMMARY
# =============================================================================
# Print concise summary of filtering results (following dc_initial_algo.py style)

print("=" * 80)
print("COMPREHENSIVE FILTERING SUMMARY")
print("=" * 80)

# Synapse dataframe updates
print(f"\n SYNAPSE DATAFRAME UPDATES:")
print(f"  Updating synapse dataframes after cluster filtering...")
print(f"  E synapses: {len(syn_exec_df)} -> {len(syn_exec_df_filtered)} (filtered)")
print(f"  I synapses: {len(syn_inh_df)} -> {len(syn_inh_df_filtered)} (filtered)")
print(f"  Adding I synapse cluster information to E synapse dataframe...")
print(f"   Synapse dataframes updated after filtering")

print(f"\n FILTERED INHIBITORY SYNAPSE DATAFRAME:")
print(f"  Shape: {syn_inh_df_filtered.shape}")
print(f"  Columns: {list(syn_inh_df_filtered.columns)}")

# E synapse filtering summary
print(f"\n EXCITATORY SYNAPSES:")
print(f"  Initial E synapses: {len(syn_exec_df)}")
print(f"  E synapses after clustering and filtering: {len(syn_exec_df_filtered)}")  # All E synapses are clustered
print(f"  E synapses in valid clusters: {len(syn_exec_df)-len(syn_exec_df_filtered)}")  # Use filtered count

# E cluster filtering summary
print(f"\n EXCITATORY CLUSTERS:")
print(f"  Initial E clusters found: {len(unique_peaks)}")
print(f"  E clusters after density filtering: {len(cluster_df)}")
print(f"  E clusters filtered out: {len(unique_peaks) - len(cluster_df)}")

# I synapse filtering summary
print(f"\n INHIBITORY SYNAPSES:")
print(f"  Initial I synapses: {len(syn_inh_df)}")
print(f"  I synapses after distance filtering: {len(syn_inh_df_filtered)}")
print(f"  I synapses filtered out: {len(syn_inh_df) - len(syn_inh_df_filtered)}")

# I cluster filtering summary
print(f"\n INHIBITORY CLUSTERS:")
print(f"  Initial I clusters found: {len(clusters_dict_inh)}")
print(f"  I clusters after distance filtering: {len(syn_inh_cluster_df_filtered)}")
print(f"  I clusters filtered out: {len(clusters_dict_inh) - len(syn_inh_cluster_df_filtered)}")

# Cutoff information
print(f"\n CUTOFF INFORMATION:")
print(f"  Overall density: {overall_density:.5f} synapses/μm")
print(f"  Dynamic cutoff: {dynamical_cutoff:.3f} μm")
print(f"  Cable length: {neuron.cable_length:.2f} μm")

# E/I association summary
print(f"\n E/I ASSOCIATION:")
print(f"  E clusters with I synapses: {len(cluster_df[cluster_df['i_synapse_count'] > 0])}")
print(f"  Total I synapses mapped to E clusters: {cluster_df['i_synapse_count'].sum()}")
print(f"  Total I clusters mapped to E clusters: {cluster_df['i_cluster_count'].sum()}")

print("\n" + "=" * 80)
print(" COMPREHENSIVE FILTERING SUMMARY COMPLETED")
print("=" * 80)


COMPREHENSIVE FILTERING SUMMARY

 SYNAPSE DATAFRAME UPDATES:
  Updating synapse dataframes after cluster filtering...
  E synapses: 959 -> 557 (filtered)
  I synapses: 464 -> 146 (filtered)
  Adding I synapse cluster information to E synapse dataframe...
   Synapse dataframes updated after filtering

 FILTERED INHIBITORY SYNAPSE DATAFRAME:
  Shape: (146, 20)
  Columns: ['Unnamed: 0', 'id', 'Ipos3DX', 'Ipos3DY', 'Ipos3DZ', 'syn_size', 'pre_identity', 'pre_type', 'isOnSpine', 'SynapseVolume', 'closest_node_id', 'distance_to_node', 'cluster_id', 'closest_e_syn_id', 'min_dist_e_syn_tot', 'cluster_id_exec', 'cluster_id_inh_old', 'cluster_id_inh', 'min_dist_e_syn_in_clu', 'distance_to_soma']

 EXCITATORY SYNAPSES:
  Initial E synapses: 959
  E synapses after clustering and filtering: 557
  E synapses in valid clusters: 402

 EXCITATORY CLUSTERS:
  Initial E clusters found: 586
  E clusters after density filtering: 206
  E clusters filtered out: 380

 INHIBITORY SYNAPSES:
  Initial I synapses

In [26]:
cluster_df
# Display final I cluster dataframe


e_cluster_id  Cluster_Peak  e_synapse_count                     Synapses  \
0               0            17                2                 [2998, 3305]   
2               2           127                2               [19524, 19539]   
7               7           327                2               [29653, 29651]   
13             13           455                2                      [14, 4]   
14             14           546                6  [106, 108, 83, 131, 96, 83]   
..            ...           ...              ...                          ...   
573           573         30935                2               [30907, 30925]   
578           578         31087                2               [31082, 31081]   
580           580         31168                2               [31156, 31167]   
582           582         31347                2               [31343, 31340]   
585           585         31493                3        [31486, 31475, 31491]   

              Associated_Nodes  minimal_cable_length  cluster_density  \
0                 [3402, 3707]              2.106119         0.949614   
2               [19709, 19724]              1.525316         1.311203   
7               [29688, 29690]              0.201516         9.924781   
13                  [450, 460]              1.002442         1.995127   
14   [529, 542, 552, 554, 577]              4.819118         1.245041   
..                         ...                   ...              ...   
573             [30917, 30935]              1.855205         1.078048   
578             [31086, 31087]              0.100220        19.956012   
580             [31161, 31172]              1.102288         1.814408   
582             [31345, 31348]              0.299933         6.668166   
585      [31478, 31489, 31494]              1.624525         1.846694   

     i_synapse_count  has_I_associated  i_cluster_count  
0                  0             False                0  
2                  0             False                0  
7                  1              True                1  
13                 1              True                1  
14                 0             False                0  
..               ...               ...              ...  
573                1              True                1  
578                1              True                1  
580                0             False                0  
582                0             False                0  
585                1              True                1  

[206 rows x 10 columns]

In [27]:
# =============================================================================
# 19. VISUALIZATION SYSTEM
# =============================================================================
# Create comprehensive visualizations using the new visualization system

from pathlib import Path
import importlib
import src.visualization.visualization_orchestrator
import src.visualization.cluster_visualization
importlib.reload(src.visualization.visualization_orchestrator)
importlib.reload(src.visualization.cluster_visualization)
from src.visualization.visualization_orchestrator import create_all_visualizations
from src.visualization.visualization_config import create_visualization_config

# Set up visualization output directory
figures_base_dir = (PROJECT_ROOT / "figures" / "microns" / cfg.input.neuron_id).resolve()
figures_base_dir.mkdir(parents=True, exist_ok=True)

print(f"Visualization output directory: {figures_base_dir}")

# Create all visualizations
print("\n" + "="*60)
print("CREATING ALL VISUALIZATIONS")
print("="*60)

figures = create_all_visualizations(
    syn_exec_df=syn_exec_df_filtered,
    syn_inh_df=syn_inh_df_filtered,
    calculation_nodes=calculation_nodes,
    node_counts=node_counts,
    neuron_skel=neuron,
    neuron_id=cfg.input.neuron_id,
    output_base_dir=figures_base_dir,
    cluster_df=cluster_df,  # Add cluster information for cluster visualizations
    show_inhibitory=True,
    save_plots=True
)

print(f"\n Visualization system completed successfully!")
print(f"Created {len(figures)} visualizations in: {figures_base_dir}")

# Create distance to soma visualization
print("\n" + "="*60)
print("CREATING DISTANCE TO SOMA VISUALIZATION")
print("="*60)

from src.visualization.synapse_plots import plot_distance_to_soma

config = create_visualization_config(
    base_output_dir=figures_base_dir,
    neuron_id=cfg.input.neuron_id
)

figures_1 = plot_distance_to_soma(syn_exec_df, syn_inh_df, neuron, config, True)
print(" Distance to soma visualization completed successfully!")


Visualization output directory: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3

CREATING ALL VISUALIZATIONS


INFO  : Using "plotly" backend for 3D plotting. (navis)
INFO  : Use the `.show()` method to plot the figure. (navis)


Saved synapse visualization: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3/synapses/n3_synapses_3d_both.png


INFO  : Use the `.show()` method to plot the figure. (navis)
INFO	navis:ddd.py:plot3d_plotly()- Use the `.show()` method to plot the figure.


Saved node counts visualization: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3/nodes/n3_node_counts_synapses.png


...

Saved cluster visualization: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3/clusters/n3_clusters_synapse_count.png


INFO  : Use the `.show()` method to plot the figure. (navis)
INFO	navis:ddd.py:plot3d_plotly()- Use the `.show()` method to plot the figure.


Saved cluster density visualization: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3/clusters/n3_clusters_density.png

 Created 7 visualizations successfully!

 Visualization system completed successfully!
Created 7 visualizations in: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3

CREATING DISTANCE TO SOMA VISUALIZATION


/home/ge95zic/miniconda3/envs/dendric311/lib/python3.11/site-packages/scipy/stats/_stats_py.py:6277: RuntimeWarning:

invalid value encountered in scalar subtract

/home/ge95zic/miniconda3/envs/dendric311/lib/python3.11/site-packages/scipy/stats/_stats_py.py:6831: RuntimeWarning:

invalid value encountered in scalar subtract



Distance to soma mean E synapse:  inf
Distance to soma mean I synapse:  inf
Saved distance to soma visualization: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3/synapses/n3_distance_to_soma_syn_type.png
 Distance to soma visualization completed successfully!


In [28]:
# =============================================================================
# 20. HISTOGRAM VISUALIZATIONS
# =============================================================================
# Create comprehensive histogram visualizations for statistical analysis
#
# IMPORTANT: Make sure you're using the 'dendric311' conda environment/kernel
# If you get import errors, check that your Jupyter kernel is set to 'dendric311'

import pandas as pd
import numpy as np
from pathlib import Path
import importlib

# Import histogram visualization functions
import src.visualization.histogram_plots
importlib.reload(src.visualization.histogram_plots)
importlib.reload(src.visualization.visualization_orchestrator)
importlib.reload(src.visualization.advanced_histogram_plots)
from src.visualization.visualization_orchestrator import create_histogram_visualizations, create_advanced_histogram_visualizations

print("\n" + "="*60)
print("CREATING HISTOGRAM VISUALIZATIONS")
print("="*60)

# Note: The following histogram visualizations require additional data that would be generated
# in the inhibitory analysis section. For now, we'll show the structure and comment out
# the actual execution until the required data is available.

"""
# Create histogram visualizations
# (Uncomment when inhibitory analysis data is available)

histogram_figures = create_histogram_visualizations(
    cluster_df=cluster_df,  # Excitatory cluster DataFrame
    cluster_df_inh=cluster_df_inh,  # Inhibitory cluster DataFrame (from inhibitory analysis)
    calculation_nodes_inh=calculation_nodes_inh,  # Inhibitory density nodes (from inhibitory analysis)
    all_synapses=all_synapses,  # Combined inhibitory synapses (from inhibitory analysis)
    dynamical_cutoff=dynamical_cutoff,  # Distance cutoff threshold (from inhibitory analysis)
    neuron_id=cfg.input.neuron_id,
    output_base_dir=figures_base_dir,
    save_plots=True
)

print(f" Created {len(histogram_figures)} histogram visualizations successfully!")
print(f"Histograms saved to: {figures_base_dir / 'histo_plots'}")
"""

print(" Histogram visualization system ready!")
print(" Histogram plots will be saved to: histo_plots/ directory")
print(" Uncomment the code above when inhibitory analysis data is available")

# Test with existing excitatory cluster data (if available)
if 'cluster_df' in locals() and cluster_df is not None:
    print("\n Creating ADVANCED histograms with I/E separation and distance distributions...")
    
    # Import the new advanced histogram function
    from src.visualization.visualization_orchestrator import create_advanced_histogram_visualizations
    
    print(f" Output directory: {figures_base_dir}")
    print(f" Histo plots directory: {figures_base_dir / 'histo_plots'}")
    
    # Check what data is available
    print(f" Available data:")
    print(f"   • cluster_df: {len(cluster_df)} excitatory clusters")
    if 'has_I_associated' in cluster_df.columns:
        i_clusters = cluster_df['has_I_associated'].sum()
        print(f"   • Clusters with I synapses: {i_clusters} ({i_clusters/len(cluster_df)*100:.1f}%)")
    else:
        print(f"   • has_I_associated column: Not found (will create simple histograms)")
    
    # Check for inhibitory data
    inhibitory_data_available = False
    if 'syn_inh_cluster_df_filtered' in locals() and 'final_i_cluster_df' in locals():
        print(f"   • Inhibitory data: Available")
        inhibitory_data_available = True
    else:
        print(f"   • Inhibitory data: Not available (will skip inhibitory histograms)")
    
    try:
        # Create advanced histograms with available data
        advanced_figures = create_advanced_histogram_visualizations(
            cluster_df=cluster_df,
            neuron_id=cfg.input.neuron_id,
            output_base_dir=figures_base_dir,
            # Add inhibitory data if available
            cluster_df_inh=final_i_cluster_df if inhibitory_data_available else None,
            
            syn_inh_df_filtered=syn_inh_df_filtered if inhibitory_data_available else None,
            dynamical_cutoff=1.0/overall_density if 'overall_density' in locals() else None,
            geodesic_mat_full=geodesic_mat_full if 'geodesic_mat_full' in locals() else None,
            save_plots=True
        )
        
        print(f" Successfully created {len(advanced_figures)} advanced histograms!")
        print(" Created histograms:")
        for name, fig in advanced_figures.items():
            print(f"   • {name}")
            
        # Show the first histogram as an example
        first_fig = list(advanced_figures.values())[0]
        first_fig.show()
        
    except Exception as e:
        print(f" Error creating advanced histograms: {e}")
        print(" This might be because cluster_df doesn't have the expected column names")
        print(" Available columns in cluster_df:", list(cluster_df.columns) if 'cluster_df' in locals() else "cluster_df not found")
        import traceback
        traceback.print_exc()
else:
    print("ℹ  No cluster_df available for testing")





CREATING HISTOGRAM VISUALIZATIONS
 Histogram visualization system ready!
 Histogram plots will be saved to: histo_plots/ directory
 Uncomment the code above when inhibitory analysis data is available

 Creating ADVANCED histograms with I/E separation and distance distributions...
 Output directory: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3
 Histo plots directory: /home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/figures/microns/n3/histo_plots
 Available data:
   • cluster_df: 206 excitatory clusters
   • Clusters with I synapses: 101 (49.0%)
   • Inhibitory data: Available
Creating all advanced histogram visualizations...
 Using provided dynamical cutoff: 3.351 μm

 Creating excitatory e_synapse_count histogram with I separation...

 E_SYNAPSE_COUNT STATISTICS:
  Total clusters: 206
  Clusters with I synapses: 101 (49.0%)
  Clusters without I synapses: 105 (51.0%)
  With I - Mean: 2.84, Median: 3.00
  Without I - Mean: 2.57, Median: 2.00
Saved ex

In [29]:
cluster_df

e_cluster_id  Cluster_Peak  e_synapse_count                     Synapses  \
0               0            17                2                 [2998, 3305]   
2               2           127                2               [19524, 19539]   
7               7           327                2               [29653, 29651]   
13             13           455                2                      [14, 4]   
14             14           546                6  [106, 108, 83, 131, 96, 83]   
..            ...           ...              ...                          ...   
573           573         30935                2               [30907, 30925]   
578           578         31087                2               [31082, 31081]   
580           580         31168                2               [31156, 31167]   
582           582         31347                2               [31343, 31340]   
585           585         31493                3        [31486, 31475, 31491]   

              Associated_Nodes  minimal_cable_length  cluster_density  \
0                 [3402, 3707]              2.106119         0.949614   
2               [19709, 19724]              1.525316         1.311203   
7               [29688, 29690]              0.201516         9.924781   
13                  [450, 460]              1.002442         1.995127   
14   [529, 542, 552, 554, 577]              4.819118         1.245041   
..                         ...                   ...              ...   
573             [30917, 30935]              1.855205         1.078048   
578             [31086, 31087]              0.100220        19.956012   
580             [31161, 31172]              1.102288         1.814408   
582             [31345, 31348]              0.299933         6.668166   
585      [31478, 31489, 31494]              1.624525         1.846694   

     i_synapse_count  has_I_associated  i_cluster_count  
0                  0             False                0  
2                  0             False                0  
7                  1              True                1  
13                 1              True                1  
14                 0             False                0  
..               ...               ...              ...  
573                1              True                1  
578                1              True                1  
580                0             False                0  
582                0             False                0  
585                1              True                1  

[206 rows x 10 columns]

In [35]:
# =============================================================================
# 21. STATISTICAL COMPARISON VISUALIZATIONS
# =============================================================================
# Create statistical comparison plots for cluster properties using Mann-Whitney U tests
# Comparing clusters with and without inhibitory synapses

print("=" * 80)
print("CREATING STATISTICAL COMPARISON VISUALIZATIONS")
print("=" * 80)

try:
    importlib.reload(src.visualization.visualization_orchestrator)
    from src.visualization.visualization_orchestrator import create_statistical_comparison_visualizations
    from pathlib import Path
    
    # Set up output directory
    output_base_dir = Path("../figures/microns/n3")
    
    print(f" Output directory: {output_base_dir}")
    print(f" Available data:")
    print(f"   • cluster_df: {len(cluster_df)} excitatory clusters")
    print(f"   • Clusters with I synapses: {len(cluster_df[cluster_df['has_I_associated']])} ({len(cluster_df[cluster_df['has_I_associated']])/len(cluster_df)*100:.1f}%)")
    print(f"   • Clusters without I synapses: {len(cluster_df[~cluster_df['has_I_associated']])} ({len(cluster_df[~cluster_df['has_I_associated']])/len(cluster_df)*100:.1f}%)")
    
    # Create statistical comparison visualizations
    print("\n Creating statistical comparison visualizations...")
    statistical_figures = create_statistical_comparison_visualizations(
        cluster_df=cluster_df,
        neuron_id="n3",
        output_base_dir=output_base_dir,
        save_plots=True
    )
    
    print(f"\n Created {len(statistical_figures)} statistical comparison plots successfully!")
    print(" Created statistical comparisons:")
    for name, fig in statistical_figures.items():
        print(f"   • {name}")
    
    # Show the first plot as an example
    if statistical_figures:
        first_fig = list(statistical_figures.values())[0]
        first_fig.show()
        
except Exception as e:
    print(f" Error creating statistical comparison visualizations: {e}")
    print(" This might be because cluster_df doesn't have the expected column names")
    print(" Available columns in cluster_df:", list(cluster_df.columns) if 'cluster_df' in locals() else "cluster_df not found")
    import traceback
    traceback.print_exc()


CREATING STATISTICAL COMPARISON VISUALIZATIONS
 Output directory: ../figures/microns/n3
 Available data:
   • cluster_df: 206 excitatory clusters
   • Clusters with I synapses: 101 (49.0%)
   • Clusters without I synapses: 105 (51.0%)

 Creating statistical comparison visualizations...
Saved cable length comparison: ../figures/microns/n3/t_test_violin/n3_excitatory_cable_length_with_vs_without_inhibitory.png
Saved synapse count comparison: ../figures/microns/n3/t_test_violin/n3_excitatory_synapse_count_with_vs_without_inhibitory.png
Saved cluster density comparison: ../figures/microns/n3/t_test_violin/n3_excitatory_cluster_density_with_vs_without_inhibitory.png

 Created 3 statistical comparison plots successfully!

 Created 3 statistical comparison visualizations successfully!

 Created 3 statistical comparison plots successfully!
 Created statistical comparisons:
   • cable_length_comparison
   • synapse_count_comparison
   • density_comparison


In [147]:
# =============================================================================
# 22. INTRA-INTER CLUSTER DISTANCE ANALYSIS
# =============================================================================

import importlib
import src.processing.cluster_processing as cluster_processing
importlib.reload(cluster_processing)

from src.processing.cluster_processing import (
    compute_intra_cluster_distances,
    compute_inter_cluster_distances
)

# Compute intra-cluster and inter-cluster distances
cluster_df = compute_intra_cluster_distances(cluster_df, syn_exec_df, geodesic_mat_full)
cluster_df = compute_inter_cluster_distances(cluster_df, syn_exec_df, geodesic_mat_full)


In [159]:
# MAKE A CORRECT VISUALIZATION

# # =============================================================================
# # 23. INTRA-INTER CLUSTER DISTANCE VISUALIZATIONS
# # =============================================================================
# # Create visualizations for intra-cluster vs inter-cluster distance analysis

# print("=" * 80)
# print(
# "CREATING INTRA-INTER CLUSTER DISTANCE VISUALIZATIONS")
# print("=" * 80)

# try:
#     from src.visualization.visualization_orchestrator import create_intra_inter_distance_visualizations
#     from pathlib import Path
    
#     # Set up output directory
#     output_base_dir = Path("../figures/microns/n3")
    
#     print(f" Output directory: {output_base_dir}")
#     print(f" Available data:")
#     print(f"   • cluster_df: {len(cluster_df)} excitatory clusters")
    
#     # Check if required columns exist
#     required_cols = ['median_intra_dist', 'inter_median_dist']
#     missing_cols = [col for col in required_cols if col not in cluster_df.columns]
    
#     if missing_cols:
#         print(f"  Missing required columns: {missing_cols}")
#         print("   Please run the intra-inter cluster distance analysis cell first")
#     else:
#         print(f"   • Clusters with intra distances: {len(cluster_df[cluster_df['median_intra_dist'] > 0])}")
#         print(f"   • Clusters with inter distances: {len(cluster_df.dropna(subset=['inter_median_dist']))}")
        
#         # Create visualizations
#         print(f"\n Creating intra-inter distance visualizations...")
#         intra_inter_figures = create_intra_inter_distance_visualizations(
#             cluster_df=cluster_df,
#             neuron_id="n3",
#             output_base_dir=output_base_dir,
#             save_plots=True
#         )
        
#         print(f"\n Created {len(intra_inter_figures)} intra-inter distance visualizations successfully!")
#         print(f" Created visualizations:")
#         for name, fig in intra_inter_figures.items():
#             print(f"   • {name}")
        
#         # Display the main comparison plot
#         if 'intra_vs_inter_comparison' in intra_inter_figures:
#             print(f"\n Displaying intra vs inter cluster distance comparison...")
#             intra_inter_figures['intra_vs_inter_comparison'].show()
    
# except Exception as e:
#     print(f" Error creating intra-inter distance visualizations: {e}")
#     import traceback
#     traceback.print_exc()
    

In [167]:
# =============================================================================
# 24. BRANCH ANALYSIS
# =============================================================================
# Complete branch analysis: splitting, filtering, and statistics
importlib.reload(src.processing.branch_processing)
from src.processing.branch_processing import (
    split_branches,
    build_branch_dataframe,
    filter_branches_by_length,
    add_volume_metrics,
    get_branches_with_both_synapse_types,
    print_branch_filtering_summary
)

def run_complete_branch_analysis(
    neuron_skel,
    syn_exec_df: pd.DataFrame,
    syn_inh_df: pd.DataFrame,
    percentile_cutoff: float = 0.05
) -> tuple:
    """
    Run complete branch analysis workflow.
    
    Args:
        neuron_skel: Neuron skeleton object
        syn_exec_df: DataFrame with excitatory synapse data
        syn_inh_df: DataFrame with inhibitory synapse data
        percentile_cutoff: Percentile cutoff for filtering (default 0.05)
        
    Returns:
        Tuple of (neuron_splits, branch_df, filtered_branch_df, filter_stats, branches_with_both)
    """
    print(" Starting complete branch analysis...")
    
    # 1) Split neuron into branches at branchpoints
    print("\n Splitting neuron into branches...")
    neuron_splits, junctions_list = split_branches(neuron_skel)
    print(f"   • Total branches created: {len(neuron_splits)}")
    print(f"   • Junction nodes identified: {len(junctions_list)}")
    
    # 2) Build branch DataFrame with synapse statistics
    print("\n Building branch DataFrame...")
    branch_df = build_branch_dataframe(neuron_splits, syn_exec_df, syn_inh_df)
    print(f"   • Branch DataFrame shape: {branch_df.shape}")
    print(f"   • Columns: {list(branch_df.columns)}")
    
    # 3) Display basic statistics
    print(f"\n Branch Statistics:")
    print(f"   • Total branches: {len(branch_df)}")
    print(f"   • Branches with E-synapses: {len(branch_df[branch_df['n_e'] > 0])}")
    print(f"   • Branches with I-synapses: {len(branch_df[branch_df['n_i'] > 0])}")
    print(f"   • Branches with both types: {len(branch_df[(branch_df['n_e'] > 0) & (branch_df['n_i'] > 0)])}")
    print(f"   • Total E-synapses across all branches: {branch_df['n_e'].sum()}")
    print(f"   • Total I-synapses across all branches: {branch_df['n_i'].sum()}")
    
    # 4) Filter branches by length using percentile cutoff
    print(f"\n Filtering branches by length (cutoff: {percentile_cutoff*100}th percentile)...")
    filtered_branch_df, filter_stats = filter_branches_by_length(branch_df, percentile_cutoff)
    
    # 5) Print filtering summary
    print_branch_filtering_summary(filter_stats)
    
    # 6) Add volume metrics to filtered branches
    print("\n Adding volume metrics...")
    filtered_branch_df = add_volume_metrics(filtered_branch_df, syn_exec_df, syn_inh_df)
    
    # 7) Get branches with both synapse types
    branches_with_both = get_branches_with_both_synapse_types(filtered_branch_df)
    print(f"\n Branches with both E and I synapses: {len(branches_with_both)}")
    
    # 8) Display updated statistics
    print(f"\n Filtered Branch Statistics:")
    print(f"   • Remaining branches: {len(filtered_branch_df)}")
    print(f"   • Remaining E-synapses: {filtered_branch_df['n_e'].sum()}")
    print(f"   • Remaining I-synapses: {filtered_branch_df['n_i'].sum()}")
    print(f"   • Branches with both types: {len(branches_with_both)}")
    
    print("\n Branch analysis completed successfully!")
    
    return junctions_list,neuron_splits, branch_df, filtered_branch_df, filter_stats, branches_with_both

# Run the complete branch analysis
junctions_list, neuron_splits, branch_df, filtered_branch_df, filter_stats, branches_with_e_and_i = run_complete_branch_analysis(
    neuron_skel=neuron,
    syn_exec_df=syn_exec_df,
    syn_inh_df=syn_inh_df,
    percentile_cutoff=0.05
)

# Display first few rows of filtered data
print(f"\n First 5 filtered branches:")
display(filtered_branch_df.head())


 Starting complete branch analysis...

 Splitting neuron into branches...
   • Total branches created: 450
   • Junction nodes identified: 449

 Building branch DataFrame...
   • syn_exec_df columns: ['Exec_syn_id', 'id', 'Epos3DX', 'Epos3DY', 'Epos3DZ', 'syn_size', 'pre_identity', 'pre_type', 'isOnSpine', 'SynapseVolume', 'closest_node_id', 'distance_to_node', 'cluster_id', 'distance_to_soma']
   • syn_inh_df columns: ['Inh_syn_id', 'id', 'Ipos3DX', 'Ipos3DY', 'Ipos3DZ', 'syn_size', 'pre_identity', 'pre_type', 'isOnSpine', 'SynapseVolume', 'closest_node_id', 'distance_to_node', 'cluster_id', 'closest_e_syn_id', 'min_dist_e_syn_tot', 'cluster_id_exec', 'cluster_id_inh_old', 'cluster_id_inh', 'min_dist_e_syn_in_clu', 'distance_to_soma']
   • Using exec_id_col: Exec_syn_id
   • Using inh_id_col: Inh_syn_id
   • Branch DataFrame shape: (450, 7)
   • Columns: ['branch_idx', 'junction_id', 'branch_length', 'n_e', 'n_i', 'e_syn_ids', 'i_syn_ids']

 Branch Statistics:
   • Total branches: 450

branch_idx  junction_id  branch_length  n_e  n_i e_syn_ids i_syn_ids  \
0           0          309       2.188072    1    0     [366]        []   
1           1          336       2.165487    1    0     [923]        []   
2           2          340       2.756777    1    0     [275]        []   
3           3          354       2.402047    1    0     [368]        []   
4           4          372       1.613429    1    0     [103]        []   

   exec_vol_sum  inh_vol_sum  total_syn  
0      0.095648          0.0          1  
1      0.139072          0.0          1  
2      0.070768          0.0          1  
3      0.015184          0.0          1  
4      0.073920          0.0          1

In [168]:
# =============================================================================
# 25. BRANCH VISUALIZATIONS
# =============================================================================
# Create comprehensive branch analysis visualizations

importlib.reload(src.visualization.visualization_orchestrator)
from src.visualization.visualization_orchestrator import create_branch_visualizations

# Create branch visualizations
branch_visualizations = create_branch_visualizations(
    neuron_splits=neuron_splits,
    branch_df=branch_df,
    filtered_branch_df=filtered_branch_df,
    filter_stats=filter_stats,
    syn_exec_df=syn_exec_df,
    syn_inh_df=syn_inh_df,
    neuron_skel=neuron,
    junctions_list=junctions_list,
    calculation_nodes=calculation_nodes,
    neuron_id=cfg.input.neuron_id,
    output_base_dir=output_base_dir,
    save_plots=True
)

print(f"\n Branch visualizations created:")
for viz_name, fig in branch_visualizations.items():
    print(f"   • {viz_name}")

# Display the visualizations
print(f"\n Displaying branch visualizations...")

# 1. Branch length distribution
if 'branch_length_distribution' in branch_visualizations:
    print(f"\n Branch Length Distribution:")
    branch_visualizations['branch_length_distribution'].show()

# 2. Branch points 3D visualization
if 'branch_points_3d' in branch_visualizations:
    print(f"\n Branch Points 3D Visualization:")
    branch_visualizations['branch_points_3d'].show()

# 3. Branch volume correlation
if 'branch_volume_correlation' in branch_visualizations:
    print(f"\n Branch Volume Correlation:")
    branch_visualizations['branch_volume_correlation'].show()

# 4. Branch synapse count correlation
if 'branch_synapse_count_correlation' in branch_visualizations:
    print(f"\n Branch Synapse Count Correlation:")
    branch_visualizations['branch_synapse_count_correlation'].show()

# 5. Branch filtering summary
if 'branch_filtering_summary' in branch_visualizations:
    print(f"\n Branch Filtering Summary:")
    branch_visualizations['branch_filtering_summary'].show()

print(f"\n Branch visualizations completed successfully!")



 Creating branch analysis visualizations...
 Creating branch length distribution plot...
Branch length distribution plot saved to: ../figures/microns/n3/branches/n3_branch_length_distribution.png
 Creating branch points 3D visualization...


Branch points 3D plot saved to: ../figures/microns/n3/branches/n3_branch_points_3d.png
 Creating branch volume correlation plot...
Branch volume correlation plot saved to: ../figures/microns/n3/branches/n3_branch_volume_correlation.png
 Creating branch synapse count correlation plot...
Branch synapse count correlation plot saved to: ../figures/microns/n3/branches/n3_branch_synapse_count_correlation.png
 Creating branch filtering summary plot...
Branch filtering summary plot saved to: ../figures/microns/n3/branches/n3_branch_filtering_summary.png

 Created 5 branch analysis visualizations successfully!

 Branch visualizations created:
   • branch_length_distribution
   • branch_points_3d
   • branch_volume_correlation
   • branch_synapse_count_correlation
   • branch_filtering_summary

 Displaying branch visualizations...

 Branch Length Distribution:



 Branch Points 3D Visualization:



 Branch Volume Correlation:



 Branch Synapse Count Correlation:



 Branch Filtering Summary:



 Branch visualizations completed successfully!


In [178]:
final_i_cluster_df

i_cluster_id  i_synapse_count  i_synapses  min_distance_to_e  \
0               1                1      [8412]           0.912706   
1               2                1     [26437]           0.914857   
2               6                1         [7]           0.301963   
3              11                2  [427, 418]           0.100769   
4              12                1       [502]           2.501528   
..            ...              ...         ...                ...   
116           320                1     [31092]           0.997437   
117           327                1     [31487]           0.102159   
118         25047                1      [2028]           1.101270   
119         25048                1      [2047]           0.693294   
120        285489                1     [27100]           2.633356   

     mean_distance_to_e  max_distance_to_e  e_cluster_id  e_synapse_count  \
0              0.912706           0.912706           172                4   
1              0.914857           0.914857           489                3   
2              0.301963           0.301963            13                2   
3              0.302414           0.504060            20                6   
4              2.501528           2.501528           573                2   
..                  ...                ...           ...              ...   
116            0.997437           0.997437           578                2   
117            0.102159           0.102159           585                3   
118            1.101270           1.101270            47                3   
119            0.693294           0.693294            48                3   
120            2.633356           2.633356           489                3   

     cluster_density  minimal_cable_length  e_i_ratio  
0           1.132870              3.530854        4.0  
1           1.411292              2.125712        3.0  
2           1.995127              1.002442        2.0  
3           1.241809              4.831661        3.0  
4           1.078048              1.855205        2.0  
..               ...                   ...        ...  
116        19.956012              0.100220        2.0  
117         1.846694              1.624525        3.0  
118         1.197023              2.506218        3.0  
119         1.125086              2.666464        3.0  
120         1.411292              2.125712        3.0  

[121 rows x 11 columns]

In [181]:
# =============================================================================
# 26. ADVANCED BRANCH VISUALIZATIONS
# =============================================================================
# Create advanced branch visualizations for a specific branch
# USER CONFIGURATION: Change branch_idx to visualize different branches

# Force complete reload of modules to ensure latest changes are available
import sys
if 'src.visualization.branch_plots' in sys.modules:
    del sys.modules['src.visualization.branch_plots']
if 'src.visualization.visualization_orchestrator' in sys.modules:
    del sys.modules['src.visualization.visualization_orchestrator']

# Re-import the modules
import src.visualization.branch_plots
import src.visualization.visualization_orchestrator
importlib.reload(src.visualization.branch_plots)
importlib.reload(src.visualization.visualization_orchestrator)

from src.visualization.visualization_orchestrator import create_advanced_branch_visualizations

# Verify that all required functions are available
try:
    from src.visualization.branch_plots import (
        plot_branch_synapses_3d,
        plot_branch_synapses_by_cluster,
        plot_synapse_distance_to_soma_histogram,
        plot_branch_density_analysis,
        plot_branch_inhibitory_clusters
    )
    print(" All advanced branch visualization functions imported successfully!")
except ImportError as e:
    print(f" Import error: {e}")
    print("Please restart the kernel and try again.")

# =============================================================================
# USER CONFIGURATION - MODIFY THESE PARAMETERS AS NEEDED
# =============================================================================
branch_idx = 51  # ← CHANGE THIS: Pick  branch index here (0 to len(neuron_splits)-1)
show_plots_in_notebook = True  # ← CHANGE THIS: Set to True to display plots in notebook

print(f" Creating advanced visualizations for branch {branch_idx}")
print(f" Total branches available: {len(neuron_splits)}")
print(f" Branch {branch_idx} has {len(neuron_splits[branch_idx].nodes)} nodes")

# Create advanced branch visualizations
advanced_branch_visualizations = create_advanced_branch_visualizations(
    branch_idx=branch_idx,
    neuron_splits=neuron_splits,
    syn_exec_df=syn_exec_df,
    syn_inh_df=syn_inh_df,
    cluster_df=cluster_df,
    calculation_nodes=calculation_nodes,
    geodesic_mat_full=geodesic_mat_full,
    neuron_skel=neuron,
    cluster_df_inh=syn_inh_cluster_df if 'final_i_cluster_df' in locals() else None,
    neuron_id=cfg.input.neuron_id,
    output_base_dir=output_base_dir,
    save_plots=True
)

print(f"\n Advanced branch visualizations created:")
for viz_name, fig in advanced_branch_visualizations.items():
    print(f"   • {viz_name}")

# Display the visualizations in notebook if requested
if show_plots_in_notebook:
    print(f"\n Displaying advanced branch visualizations in notebook...")
    
    # 1. Branch synapses 3D visualization
    if 'branch_synapses_3d' in advanced_branch_visualizations:
        print(f"\n Branch {branch_idx} Synapses 3D Visualization:")
        advanced_branch_visualizations['branch_synapses_3d'].show()
    
    # 2. Branch synapses by cluster
    if 'branch_synapses_by_cluster' in advanced_branch_visualizations:
        print(f"\n Branch {branch_idx} Synapses by Cluster:")
        advanced_branch_visualizations['branch_synapses_by_cluster'].show()
    
    # 3. Synapse distance to soma histogram
    if 'synapse_distance_to_soma_histogram' in advanced_branch_visualizations:
        print(f"\n Synapse Distance to Soma Histogram:")
        advanced_branch_visualizations['synapse_distance_to_soma_histogram'].show()
    
    # 4. Branch density analysis
    if 'branch_density_analysis' in advanced_branch_visualizations:
        print(f"\n Branch {branch_idx} Density Analysis:")
        advanced_branch_visualizations['branch_density_analysis'].show()
    
    # 5. Branch inhibitory clusters
    if 'branch_inhibitory_clusters' in advanced_branch_visualizations:
        print(f"\n Branch {branch_idx} Inhibitory Clusters:")
        advanced_branch_visualizations['branch_inhibitory_clusters'].show()
    
    print(f"\n Advanced branch visualizations displayed successfully!")
else:
    print(f"\n Visualizations saved to files (not displayed in notebook)")
    print(f" Check the output directory: {output_base_dir / 'branches'}")

print(f"\n Advanced branch visualizations completed successfully!")


INFO  : Use the `.show()` method to plot the figure. (navis)
INFO	navis:ddd.py:plot3d_plotly()- Use the `.show()` method to plot the figure.


 All advanced branch visualization functions imported successfully!
 Creating advanced visualizations for branch 51
 Total branches available: 450
 Branch 51 has 341 nodes

 Creating advanced branch visualizations for branch 51...


INFO  : Use the `.show()` method to plot the figure. (navis)
INFO	navis:ddd.py:plot3d_plotly()- Use the `.show()` method to plot the figure.


Branch synapses 3D plot saved to: ../figures/microns/n3/branches/n3_branch_51_synapses_3d.png
Branch synapses by cluster plot saved to: ../figures/microns/n3/branches/n3_branch_51_synapses_by_cluster.png
 Error creating advanced branch visualizations: array must not contain infs or NaNs

 Advanced branch visualizations created:
   • branch_synapses_3d
   • branch_synapses_by_cluster

 Displaying advanced branch visualizations in notebook...

 Branch 51 Synapses 3D Visualization:


/home/ge95zic/miniconda3/envs/dendric311/lib/python3.11/site-packages/numpy/_core/function_base.py:162: RuntimeWarning:

invalid value encountered in multiply

/home/ge95zic/miniconda3/envs/dendric311/lib/python3.11/site-packages/numpy/lib/_function_base_impl.py:2908: RuntimeWarning:

invalid value encountered in subtract

Traceback (most recent call last):
  File "/home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/src/visualization/visualization_orchestrator.py", line 536, in create_advanced_branch_visualizations
    fig3 = plot_synapse_distance_to_soma_histogram(
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/ge95zic/mnt/ge95zic/dendric_clustering/refactored/src/visualization/branch_plots.py", line 624, in plot_synapse_distance_to_soma_histogram
    kde_e = gaussian_kde(e_d)
            ^^^^^^^^^^^^^^^^^
  File "/home/ge95zic/miniconda3/envs/dendric311/lib/python3.11/site-packages/scipy/stats/_kde.py", line 235, in __init__
    self.set_bandwidth(bw_method=bw_


 Branch 51 Synapses by Cluster:



 Advanced branch visualizations displayed successfully!

 Advanced branch visualizations completed successfully!
